In [ ]:
path = r"D:\Ammar's\Manaf\chest_xray"

In [ ]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

from keras.layers import Activation, Dense, Input
from keras.layers import Conv2D, Flatten
from keras.layers import Reshape, Conv2DTranspose
from keras.layers import LeakyReLU
from keras.layers import BatchNormalization
from keras.optimizers import RMSprop
from keras.models import Model
import os
import cv2
import math
import pickle
from tqdm import tqdm
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
def build_generator(inputs, image_size):
    image_resize = image_size // 4
    kernel_size = 5
    layer_filters = [128, 64, 32, 1]

    x = Dense(image_resize * image_resize * layer_filters[0])(inputs)
    x = Reshape((image_resize, image_resize, layer_filters[0]))(x)

    for filters in layer_filters:
        if filters > layer_filters[-2]:
            strides = 2
        else:
            strides = 1
        x = BatchNormalization()(x)
        x = Activation('relu')(x)
        x = Conv2DTranspose(filters=filters,
                            kernel_size=kernel_size,
                            strides=strides,
                            padding='same')(x)

    x = Activation('sigmoid')(x)
    generator = Model(inputs, x, name='generator')
    return generator

In [ ]:
def build_discriminator(inputs):
    kernel_size = 5
    layer_filters = [32, 64, 128, 256]

    x = inputs
    for filters in layer_filters:
        if filters == layer_filters[-1]:
            strides = 1
        else:
            strides = 2
        x = LeakyReLU(alpha=0.2)(x)
        x = Conv2D(filters=filters,
                   kernel_size=kernel_size,
                   strides=strides,
                   padding='same')(x)

    x = Flatten()(x)
    x = Dense(1)(x)
    x = Activation('sigmoid')(x)
    discriminator = Model(inputs, x, name='discriminator')
    return discriminator

In [ ]:
def build_and_train_models(x_train, name):
    image_size = x_train.shape[1]
    x_train = np.reshape(x_train, [-1, image_size, image_size, 1])
    x_train = x_train.astype('float32') / 255

    model_name = "dcgan_mnist"
    latent_size = 100
    batch_size = 64
    train_steps = 40000
    lr = 2e-4
    decay = 6e-8
    input_shape = (image_size, image_size, 1)
    inputs = Input(shape=input_shape, name='discriminator_input')
    discriminator = build_discriminator(inputs)
    optimizer = RMSprop(lr=lr, decay=decay)
    discriminator.compile(loss='binary_crossentropy',
                          optimizer=optimizer,
                          metrics=['accuracy'])
    discriminator.summary()
    input_shape = (latent_size, )
    inputs = Input(shape=input_shape, name='z_input')
    generator = build_generator(inputs, image_size)
    generator.summary()

    optimizer = RMSprop(lr=lr * 0.5, decay=decay * 0.5)
    discriminator.trainable = False
    adversarial = Model(inputs, 
                        discriminator(generator(inputs)),
                        name=model_name)
    adversarial.compile(loss='binary_crossentropy',
                        optimizer=optimizer,
                        metrics=['accuracy'])
    adversarial.summary()

    models = (generator, discriminator, adversarial)
    params = (batch_size, latent_size, train_steps, model_name)
    train(models, x_train, params, name)

In [ ]:
def train(models, x_train, params, name):
    generator, discriminator, adversarial = models
    batch_size, latent_size, train_steps, model_name = params
    save_interval = 5000
    noise_input = np.random.uniform(-1.0, 1.0, size=[16, latent_size])
    train_size = x_train.shape[0]
    for i in range(train_steps):
        rand_indexes = np.random.randint(0, train_size, size=batch_size)
        real_images = x_train[rand_indexes]
        noise = np.random.uniform(-1.0,
                                  1.0,
                                  size=[batch_size, latent_size])
        fake_images = generator.predict(noise)
        x = np.concatenate((real_images, fake_images))
        y = np.ones([2 * batch_size, 1])
        y[batch_size:, :] = 0.0
        loss, acc = discriminator.train_on_batch(x, y)
        log = "%d: [discriminator loss: %f, acc: %f]" % (i, loss, acc)
        noise = np.random.uniform(-1.0,
                                  1.0, 
                                  size=[batch_size, latent_size])
        y = np.ones([batch_size, 1])
        loss, acc = adversarial.train_on_batch(noise, y)
        log = "%s [adversarial loss: %f, acc: %f]" % (log, loss, acc)
        print(log)
        if (i + 1) % save_interval == 0:
            plot_images(generator,
                        noise_input=noise_input,
                        n=name,
                        show=False,
                        step=(i + 1),
                        model_name=model_name)
    generator.save((path + f'/{name}.h5'))

In [ ]:
def plot_images(generator,
                noise_input,
                n,
                show=False,
                step=0,
                model_name="gan"):
    model_name = os.path.join(path, f'{n}generated_images/')
    os.makedirs(model_name, exist_ok=True)
    
    images = generator.predict(noise_input)
    
    num_images = images.shape[0]
    image_size = images.shape[1]
    rows = int(math.sqrt(noise_input.shape[0]))
    for i in range(num_images):
        filename = os.path.join(model_name, f"%05d({i}).png" % step)
        plt.figure(figsize=(30, 30))
        plt.plot(rows, rows, i + 1)
        image = np.reshape(images[i], [image_size, image_size])
        plt.imshow(image, cmap='gray')
        plt.axis('off')
        plt.savefig(filename)
    
    if show:
        plt.show()
    else:
        plt.close('all')

In [ ]:
def test_generator(generator):
    noise_input = np.random.uniform(-1.0, 1.0, size=[16, 100])
    plot_images(generator,
                'testing',
                noise_input=noise_input,
                show=True,
                model_name="test_outputs")

In [ ]:
def load_data(image_size):
  X = []
  dir = path + '/train/NORMAL'
  for i in tqdm(os.listdir(dir)):
    img = cv2.imread(os.path.join(dir, i), cv2.IMREAD_GRAYSCALE)
    img = cv2.resize(img, (image_size, image_size))
    X.append(img)
  
  return np.array(X)

x_train = load_data(148)

100%|██████████| 100/100 [00:01<00:00, 60.58it/s]


In [ ]:
build_and_train_models(x_train, 'generator-(Normal)-148x148')

Model: "discriminator"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 discriminator_input (InputL  [(None, 148, 148, 1)]    0         
 ayer)                                                           
                                                                 
 leaky_re_lu (LeakyReLU)     (None, 148, 148, 1)       0         
                                                                 
 conv2d (Conv2D)             (None, 74, 74, 32)        832       
                                                                 
 leaky_re_lu_1 (LeakyReLU)   (None, 74, 74, 32)        0         
                                                                 
 conv2d_1 (Conv2D)           (None, 37, 37, 64)        51264     
                                                                 
 leaky_re_lu_2 (LeakyReLU)   (None, 37, 37, 64)        0         
                                                     

c:\Users\Noureen Fatima\.conda\envs\tf_2.4\lib\site-packages\keras\optimizers\optimizer_v2\rmsprop.py:135: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(RMSprop, self).__init__(name, **kwargs)


_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 z_input (InputLayer)        [(None, 100)]             0         
                                                                 
 dense_1 (Dense)             (None, 175232)            17698432  
                                                                 
 reshape (Reshape)           (None, 37, 37, 128)       0         
                                                                 
 batch_normalization (BatchN  (None, 37, 37, 128)      512       
 ormalization)                                                   
                                                                 
 activation_1 (Activation)   (None, 37, 37, 128)       0         
                                                                 
 conv2d_transpose (Conv2DTra  (None, 74, 74, 128)      409728    
 nspose)                                                         
          